In [188]:
from pymongo import MongoClient
import re
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import HashingVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from konlpy.tag import *
from konlpy.utils import pprint
import numpy as np
import lda
from sklearn.pipeline import Pipeline
import pandas as pd
import statsmodels.api as sm
from collections import Counter

In [187]:
twitter = Twitter()

In [3]:
english = re.compile(r'[a-zA-Z0-9]')

In [4]:
korean = re.compile(r'[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]')

In [178]:
mongo = MongoClient(mongo_server, 27017)
review = mongo.restaurant.review

# 서버에서 DB 불러오기

In [7]:
good_temp_list = []

In [8]:
for record in review.find({'$and' : [{'rating' : '맛있다'},{'len_review' : {'$gte': 50}}]}):
    text = re.sub(english,'',record['review'])
    if re.search(korean, text.encode('utf-8')):
        good_temp_list.append(text)

In [9]:
print len(good_temp_list)

11919


In [70]:
bad_temp_list = []

In [71]:
for record in review.find({'$and' : [{'rating' : '별로'},{'len_review' : {'$gte': 50}}]}):
    text = re.sub(english,'',record['review'])
    if re.search(korean, text.encode('utf-8')):
        bad_temp_list.append(text)

In [72]:
print len(bad_temp_list)

1311


In [179]:
pipelines = []
pipelines.append({'$group': {'_id': '$restaurant_name','review':{'$addToSet':'$review'}}})
result = review.aggregate(pipelines)

In [180]:
seoul_restaurant_reviews = []
for doc in result:
    seoul_restaurant_reviews.append(doc)

# 전처리 - stemming

In [85]:
def do_stemming(reviews):
    result_list = []
    for i in range(len(reviews)):
        a = re.sub(' ','s',reviews[i])    #띄어쓰기 위해 s 붙힘
        b = twitter.pos(a, stem = True, norm= True)  #형태소 분석
        string = ''
        for word in b:                #문장으로 합침
            string += word[0]
        c = re.sub('s',' ',string)    #띄어쓰기 분리
        result_list.append(c)
    return result_list

In [90]:
result_list = do_stemming(good_temp_list)

In [91]:
bad_result_list = do_stemming(bad_temp_list)

In [92]:
len(result_list)

11919

In [93]:
len(bad_result_list)

1311

In [100]:
service_good_feature = {'서비스':['좋','친절','괜찮','최고','빠르','짱','훌륭','추천','감사','구수','최상','대박','훈훈','특별','개이득','최고','만족','세련','최고','감동'],'사장':['친절','스윗','센스'],'알바':['친절','스윗','센스'],'직원': ['친절','스윗','센스']}

In [192]:
service_bad_feature = {'서비스': ['아쉽','최악','나쁘','느리','빡치','비추','별로','그냥','낙제','쏘다쏘다','엉망','실망','불친절','문제','컴플레인','거지','그닥','그다지','구려','불편','엉성','헬','개판'],'알바':['불친절','똑바로','재수'],'사장':['불친절','똑바로','재수'],'직원':['불친절','똑바로','재수']}

In [102]:
taste_good_feature = {'간이':['맞','적절','딱','환상','담백'],'간도':['맞','적절','딱','환상','담백'],'음식':['깔끔'],'맛':['있']}

In [191]:
taste_bad_feature = {'간이':['세','쎄','강하다','별로'],'간도':['세','쎄','강하다','별로'],'음식':['별로','쏘다쏘다','최악'],'맛':['별로','최악']}

In [104]:
taste_good_emotion = ['고소','부드럽','신선','촉촉','싱싱','정갈']

In [105]:
taste_bad_emotion = ['싱겁','느끼다하다','짜다','느끼다','짜다','딱딱하다','차갑다']

In [106]:
cost_good_feature = {'가격': ['괜찮','착하다','저렴','적당','싸다','좋다','합리적','훌륭','최고','만족','마음','든든','알맞다','무난','괜춘','최상','최상','굿','엄지','낮'],'가성비':['괜찮','착하다','저렴','적당','싸다','좋다','합리적','훌륭','최고','만족','마음','든든','알맞다','무난','괜춘','최상','최상','굿','엄지'],'양도':['많','적당','푸다짐하고','괜찮다','넉넉','충분','든든'],'양이':['많','적당','푸다짐하고','괜찮다','넉넉','충분','든든'],'양은':['많','적당','푸다짐하고','괜찮다','넉넉','충분','든든']}

In [190]:
cost_bad_feature ={'가격': ['비싸','있다','나쁘','사악','비효율','높다','부담','아쉽','쏘다쏘다','별로','그닥','그다지','쎄','ㅎㄷㄷ','높','거품'],'가성비':['별로'],'양이':['적다','작다','아쉽','적다','다소','별로'],'양은':['적다','작다','아쉽','적다','다소','별로'],'양도':['적다','작다','아쉽','적다','다소','별로']}

In [109]:
atmosphere_good_feature = {'분위기': ['좋','괜찮','조용','깔끔','적당','깡패','굉장','아담','완벽','아기자기','고급','최고','세련','만족','아늑','훌륭','예쁘','이쁘','짱','심쿵','따뜻','깨끗','독특','매력','모던','취향저격','맘','마음','클래식','아름','인상적','귀엽','포근'], '인테리어': ['좋','괜찮','조용','깔끔','적당','깡패','굉장','아담','완벽','아기자기','고급','최고','세련','만족','아늑','훌륭','예쁘','이쁘','짱','심쿵','따뜻','깨끗','독특','매력','모던','취향저격','맘','마음','클래식','아름','인상적','귀엽','포근']}

In [110]:
atmosphere_bad_feature = {'분위기': ['나쁘다','바쁘다','어수선하다','이상하다','촌스럽다','별로','부담스럽다','시끄럽','복잡' ],'인테리어':[]}

In [111]:
visit_good_feature = {'의사':['있','충만','백프로','백프롭','많','만땅','마구','그득','만점','넘침'],'다시':['가다','오다','방문','찾다','가보다','한번','갈다','찾아가다','가야지','갈거다','방문하다보고','생각나다','방문한다면','와보고','재방문','접하다','간다면','갈다때가','먹다고프다','방문한다임','오자고','가기로','갈다생각이다','가면'],'굳이':[]}

In [112]:
visit_bad_feature = {'의사':['글쎄'],'굳이':['다시','많이','여기까지','줄서서','찾아','시키다','가다','찾다','여기','기다리다','줄을','사먹'],'다시':[]}

In [114]:
negative_word_emotion = ['안','않','못','없','아닌','아니']

In [134]:
def get_feature_keywords(feature_keywords, review):
    feature_temp = []
    for keyword in feature_keywords:
        if re.findall(keyword, review.encode('utf-8')):
            a = re.findall(keyword +'+[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+\s+[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+\s+[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+',review.encode('utf-8'))
            b = re.findall(keyword + '+\s+[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+\s+[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+',review.encode('utf-8'))
            c = re.findall('[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+\s+' + keyword +'[ㄱ-ㅎ|ㅏ-ㅣ|가-힣]+',review.encode('utf-8'))
            
            for ngram in a:
                t = ()
                feature_temp.append(t + (ngram,keyword))
            for ngram in b:
                t = ()
                feature_temp.append(t + (ngram,keyword))
            for ngram in c:
                t = ()
                feature_temp.append(t + (ngram,keyword))

    return feature_temp

In [131]:
def get_feature_emotions(feature_good_dict,feature_bad_dict, feature_temp):
    good_feature_emotion_list = []
    bad_feature_emotion_list = []
    
    for ngrams in feature_temp:
        keyword = ngrams[1]
        ngram = ngrams[0]
        is_bad_feature = None
        
        good_emotion_list = feature_good_dict[keyword]
        bad_emotion_list = feature_bad_dict[keyword]
        for emotion in good_emotion_list:
            if re.findall(emotion, ngram):
                is_bad_feature = False  
        for emotion in bad_emotion_list:
            if re.findall(emotion, ngram):
                is_bad_feature = True    
        for negative in negative_word_emotion:
            if re.findall(negative, ngram):
                if is_bad_feature == True:
                    is_bad_feature = False
                    break
                elif is_bad_feature == False:
                    is_bad_feature = True
                    break
                else:
                    is_bad_feature = True
                    break   
        if is_bad_feature:
            bad_feature_emotion_list.append(ngram)
        elif is_bad_feature == False:
            good_feature_emotion_list.append(ngram)
        else:
            pass
    return good_feature_emotion_list, bad_feature_emotion_list

In [132]:
def get_taste_emotion(taste_good_emotions, taste_bad_emotions):
    bad_taste_emotion_list = []
    good_taste_emotion_list = []
    for ngrams in taste_good_emotions:
        ngram = ngrams[0]
        is_bad_taste = False
        for negative in negative_word_emotion:
            if re.findall(negative,ngram):
                is_bad_taste = True
        if is_bad_taste:
            bad_taste_emotion_list.append(ngram)
        else:
            good_taste_emotion_list.append(ngram)
    
    for ngrams in taste_bad_emotions:
        ngram = ngrams[0]
        is_bad_taste = True
        for negative in negative_word_emotion:
            if re.findall(negative,ngram):
                is_bad_taste = False
        if is_bad_taste:
            bad_taste_emotion_list.append(ngram)
        else:
            good_taste_emotion_list.append(ngram)
            
    return good_taste_emotion_list, bad_taste_emotion_list

# Test 1: 리뷰별로 감정 분석

In [ ]:
for i, review in enumerate(bad_result_list):
    service_temp = get_feature_keywords(service_good_feature.keys(), review)
    good_service,bad_service = get_feature_emotions(service_good_feature, service_bad_feature, service_temp)

    atmosphere_temp = get_feature_keywords(atmosphere_good_feature.keys(), review)
    good_atmosphere,bad_atmosphere = get_feature_emotions(atmosphere_good_feature, atmosphere_bad_feature, atmosphere_temp)
    
    cost_temp = get_feature_keywords(cost_good_feature.keys(), review)
    good_cost,bad_cost = get_feature_emotions(cost_good_feature, cost_bad_feature, cost_temp)
    
    visit_temp = get_feature_keywords(visit_good_feature.keys(), review)
    good_visit,bad_visit = get_feature_emotions(visit_good_feature, visit_bad_feature, visit_temp)
    
    taste_temp = get_feature_keywords(taste_good_feature.keys(), review)
    good_taste,bad_taste = get_feature_emotions(taste_good_feature, taste_bad_feature, taste_temp)
    taste_good_emotion_temp = get_feature_keywords(taste_good_emotion, review)
    taste_bad_emotion_temp = get_feature_keywords(taste_bad_emotion, review)
    good_taste2, bad_taste2 = get_taste_emotion(taste_good_emotion_temp,taste_bad_emotion_temp)
    good_taste.extend(good_taste2)
    bad_taste.extend(bad_taste2)
    
    print i
    print 'good service emotions :{}'.format(len(good_service))
    for ngram in good_service:
        print ngram
    print 'bad service emotions :{}'.format(len(bad_service))
    for ngram in bad_service:
        print ngram
    print 'good atmosphere emotions :{}'.format(len(good_atmosphere))
    for ngram in good_atmosphere:
        print ngram
    print 'bad atmosphere emotions :{}'.format(len(bad_atmosphere))
    for ngram in bad_atmosphere:
        print ngram
    print 'good cost emotions :{}'.format(len(good_cost))
    for ngram in good_cost:
        print ngram
    print 'bad cost emotions :{}'.format(len(bad_cost))
    for ngram in bad_cost:
        print ngram
    print 'good visit emotions :{}'.format(len(good_visit))
    for ngram in good_visit:
        print ngram
    print 'bad visit emotions :{}'.format(len(bad_visit))
    for ngram in bad_visit:
        print ngram
    print 'good taste emotions :{}'.format(len(good_taste))
    for ngram in good_taste:
        print ngram
    print 'bad taste emotions :{}'.format(len(bad_taste))
    for ngram in bad_taste:
        print ngram
    print 

# Test 2. 서울내 음식점별로 감정 분석

In [136]:
for reviews in seoul_restaurant_reviews:
    print reviews['_id']
    reviews_list = do_stemming(reviews['review'])
    for i, review in enumerate(reviews_list):
        print review
        service_temp = get_feature_keywords(service_good_feature.keys(), review)
        good_service,bad_service = get_feature_emotions(service_good_feature, service_bad_feature, service_temp)

        atmosphere_temp = get_feature_keywords(atmosphere_good_feature.keys(), review)
        good_atmosphere,bad_atmosphere = get_feature_emotions(atmosphere_good_feature, atmosphere_bad_feature, atmosphere_temp)

        cost_temp = get_feature_keywords(cost_good_feature.keys(), review)
        good_cost,bad_cost = get_feature_emotions(cost_good_feature, cost_bad_feature, cost_temp)

        visit_temp = get_feature_keywords(visit_good_feature.keys(), review)
        good_visit,bad_visit = get_feature_emotions(visit_good_feature, visit_bad_feature, visit_temp)

        taste_temp = get_feature_keywords(taste_good_feature.keys(), review)
        good_taste,bad_taste = get_feature_emotions(taste_good_feature, taste_bad_feature, taste_temp)
        taste_good_emotion_temp = get_feature_keywords(taste_good_emotion, review)
        taste_bad_emotion_temp = get_feature_keywords(taste_bad_emotion, review)
        good_taste2, bad_taste2 = get_taste_emotion(taste_good_emotion_temp,taste_bad_emotion_temp)
        good_taste.extend(good_taste2)
        bad_taste.extend(bad_taste2)

        print i
        print 'good service emotions :{}'.format(len(good_service))
        for ngram in good_service:
            print ngram
        print 'bad service emotions :{}'.format(len(bad_service))
        for ngram in bad_service:
            print ngram
        print 'good atmosphere emotions :{}'.format(len(good_atmosphere))
        for ngram in good_atmosphere:
            print ngram
        print 'bad atmosphere emotions :{}'.format(len(bad_atmosphere))
        for ngram in bad_atmosphere:
            print ngram
        print 'good cost emotions :{}'.format(len(good_cost))
        for ngram in good_cost:
            print ngram
        print 'bad cost emotions :{}'.format(len(bad_cost))
        for ngram in bad_cost:
            print ngram
        print 'good visit emotions :{}'.format(len(good_visit))
        for ngram in good_visit:
            print ngram
        print 'bad visit emotions :{}'.format(len(bad_visit))
        for ngram in bad_visit:
            print ngram
        print 'good taste emotions :{}'.format(len(good_taste))
        for ngram in good_taste:
            print ngram
        print 'bad taste emotions :{}'.format(len(bad_taste))
        for ngram in bad_taste:
            print ngram
        print 

베테랑분식-센트럴시티 터미널
칼국수.. 굿 쫄면... 그냥 평범 만두... 굿
0
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

여기 맛남. 예전엔 별로이다 마느님이 맛있다 하다 나다.....
1
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :2
맛있다 하다 나다
마느님이 맛있다
bad taste emotions :0

칼국수가 얼마나 마싯다 하다 완전마싯다...ㅠㅠ너무마싯다ㅠㅠ음식도 빨리나오다 좋다ㅎㅎ쫄면이나 만두 등 나머지 메뉴는 그냥 저냥 평범하다 맛!
2
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

터미널에서 기다리다 우연히 먹다 이렇게 유명하다 곳인지 몰르다~ 모르다 먹다 맛있다! 자주 가다 최근에는 안 먹다 만두를 시키다보다 가성비다 별로고 맛은 정말 맛있다!
3
good s

bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

데블스도어-파미에가든
맛있다 엄청비싸다
0
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

Good beer and the burger wa  yum
1
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0


2
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

맥주종류 다양하다
3
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions

26
good service emotions :0
bad service emotions :0
good atmosphere emotions :1
방문하다곳인데 분위기도좋다
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :3
맛이있다 맛있다 먹다오다
특유 맛이있다
부드럽다 특유 맛이있다
bad taste emotions :0

이태원을 중심으로 발생하다 크래프트비어 열풍이 신세계 정용진 회장 마음에 들다..양조장 하나를 차리다 음식점을 만들다 생각을 하다 신세계가 이렇다 면에서는 발 빠르다 트렌드를 캐치업 하다 것 같다. 매장 입구에선 별의 별 맥주들을 다 팔다 매장으로 가지고 들어가다 수는 없다 하다. 피자는 토마토소스가 풍부하다 좋다 프라이드맥앤치즈는 맛없다기가 오히려 어러운 음식이고 버거도 웬만하다 수제버거집들보다 괜찮다. 맥주는 에일도 좋아하다 반주로는 라거가 훨씬 적합하다 생각하다 사람인지라.. 라거도 좀 있다 좋다.
27
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :2
맛없다기가 오히려 어러운
프라이드맥앤치즈는 맛없다기가

분위기가 영국인줄..! 일단 분위기가 크다 맥주 맛이나 기본적인 음식 맛은 나쁘다 않다. 프라이와 샐러드 시키다 가격대는 꽤 있다 편이네요~ 프라이 7천원대 멕시칸 치킨 만원대~ 양이 적다 샐러드 많이 먹다 싶다 분은 카페마마스로 ㅎㅎ
28
good service emoti

bad visit emotions :0
good taste emotions :0
bad taste emotions :0

버거나 시금치 피자는 새롭고 괜찮다 맥주맛이 뛰어나다 않다 느끼다 한번가기엔 좋다 두번가기다 애매한곳
49
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :2
맛이 뛰어나다 않다
느끼다 한번가기엔 좋다

고터근방에서 맥주 하다 잔 하다 곳 찾다 그냥 재방문. 주차하다 편하다 넓다 어떻다 메뉴 주문하다 중간이상. 적당하다 어둡다 맥주 맛도 괜찮다 편. 외국인 서버들도 유쾌해요;)
50
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

제대로되다 맥주 맛을 느끼다 수 있다 곳 시끄럽다 분위기이지만 실내가 크게 틔여있다 마냥 정신없다 않다. 안주들은 무난하지만 가격이 합리적이고, 맥주맛은 비싸다 하다정도로 맛있다 아 다만 엄청나다 웨이팅...각오하다
51
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :1
시끄럽다 분위기이지만
good cost emotions :1
무난하지만 가격

bad visit emotions :0
good taste emotions :2
맛은 있다 피자도
피자도 맛있다
bad taste emotions :0

약간 비싸다 같다 하지만 분위기낼 때는 괜찮다거 같다 특히 코스로 먹다 더 맛잇다 파스타는 로제가 개인적으로 젤 맛잇다!
18
good service emotions :0
bad service emotions :0
good atmosphere emotions :1
분위기낼 때는 괜찮다거
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

스테이크 코스 먹다 수프부터 디저트까지 다 맛없다. 스테이크가 제일 별로다. 파스타도 별로. 와인은 괜찮다. 사람많다 인테리어도 별로다. 가격은 비싸다.
19
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :1
다 맛없다

서다마을 터줏대감으로 음식과 분위기 좋다. 유럽 작다 식당에서 먹다 느낌. 가격대비 파스타 피자 다 괜찮다 서비스도 좋다편. 단 예약필수
20
good service emotions :1
괜찮다 서비스도
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0


...

good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :2
느끼다기엔 시중에서 팔다
내가 느끼다기엔

평창동에 살다 태어나다때부터 여기 자주 가다 수제비를 먹다. 일단 난 수제비를 좋아하다 편은 아니다... 그래도 갈다때마다 자다 먹다. 즉 그정도로 맛있다. 하지만... 맛이 좀 예전과 다르다 ㅠㅠ 조미료맛이 어느순간 나기 시작하다 ㅠㅠ 예전에 훨신 맛있다뎁 ㅠ 그래도 맛잇다맛잇다. 전도 맛있다!
36
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :4
맛있다뎁 ㅠ 그래도
그정도로 맛있다
훨신 맛있다뎁
전도 맛있다
bad taste emotions :0

감자전b 주차o
37
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0


38
good service emotions :0
bad service emoti

불친절하지만 맛있다
0
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :1
불친절하지만 맛있다
bad taste emotions :0

콜라겐의 유혹
1
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

너무 달다 몇입 못먹다더
2
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

맛있다, 다르다 향이다르다
3
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad 

ju t ok pizza. it could be better but  till pretty good for gangnam area.
0
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

Great food and great atmo phere. Will be coming here very often.
1
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :0

Not a  good a  I remembered thi  place to be. The pomodoro and  everal diff type of pizza  (margherita and  ome other one). A good meal and will probably come back but not completely  ati fied.
2
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emoti

bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :0
bad taste emotions :1
맛이 아주좋다건 아니다

옥인피자
홀릭분들의 추천레스토랑 top10에 들어가다 가보다 곳! 솔직하다 맛보다 분위기가 정말 좋다 한옥에 내부는 매우 아늑한 분위기 빛도 은은하다 아지트에 있다 느끼다. 외국인 친구랑 함께 가다 좋아하다 시그니처 메뉴 단호박 피자는 맛있다 생각보다 평범하다맛이다 알볼로피자의 단호박피자와 매우 비슷하다 맛! 차이점을 꼽자면 옥인피자는 알볼로보다 더욱 치즈와 단호박에만 집중하다 더 부드럽다 맛이다 은은하다 달고 부드럽다 젊다 여성들이 좋아하다 맛 세트메뉴로 시키다 여자 둘이서 먹기에는 많다 양이다
0
good service emotions :0
bad service emotions :0
good atmosphere emotions :1
분위기가 정말 좋다
bad atmosphere emotions :0
good cost emotions :1
많다 양이다
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :6
맛있다 생각보다 평범하다맛이다
피자는 맛있다
부드럽다 맛이다 은은하다
부드럽다 젊다 여성들이
더 부드럽다
달고 부드럽다
bad taste emotions :0

사진을 발견하다 또 올리다^^ 맛남다^-^
1
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotion

good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :3
맛있다 많이 먹다
진짜 맛있다
자체가 맛있다
bad taste emotions :0

진짜 먹다 싶다 단호박치즈피자를 엄마,아빠와 함께 먹다 오다! 기대하다 만큼은 단호박의 맛이 진하다 않다 고소하다 치즈가 풍부하다 들다 도우도 엄청 바삭하다~리코타치즈 샐러드는 신선하다 괜찮다~ 단호박이 진하다 않다 아쉽다 두 번 오진 않다 해요! 주인분들이 무척 친절하다 가게 분위기도 좋다~
41
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :2
고소하다 치즈가 풍부하다
샐러드는 신선하다
bad taste emotions :2
맛이 진하다 않다
않다 고소하다

단호박피자세트랑 스웨덴 맥주 같이 시키다 먹다 넘다 짜다 않다 단호박도 덩어리가 아니다 크림이라서 넘다 맛있다 자다 먹다~
42
good service emotions :0
bad service emotions :0
good atmosphere emotions :0
bad atmosphere emotions :0
good cost emotions :0
bad cost emotions :0
good visit emotions :0
bad visit emotions :0
good taste emotions :4
맛있

# Test 3. 음식점 별로 속성별 감정지수 파악

In [186]:
check_division = lambda x, y: y if y ==0 else round((x / float(y)),2)

for i, reviews in enumerate(seoul_restaurant_reviews):
    restaurant_good_service_count = 0
    restaurant_bad_service_count = 0
    restaurant_good_atmosphere_count =0
    restaurant_bad_atmosphere_count =0
    restaurant_good_cost_count =0
    restaurant_bad_cost_count =0
    restaurant_good_visit_count = 0
    restaurant_bad_visit_count = 0
    restaurant_good_taste_count = 0
    restaurant_bad_taste_count = 0
    print i, reviews['_id']
    reviews_list = do_stemming(reviews['review'])
    for j, review in enumerate(reviews_list):
        #print review
        service_temp = get_feature_keywords(service_good_feature.keys(), review)
        good_service,bad_service = get_feature_emotions(service_good_feature, service_bad_feature, service_temp)

        atmosphere_temp = get_feature_keywords(atmosphere_good_feature.keys(), review)
        good_atmosphere,bad_atmosphere = get_feature_emotions(atmosphere_good_feature, atmosphere_bad_feature, atmosphere_temp)

        cost_temp = get_feature_keywords(cost_good_feature.keys(), review)
        good_cost,bad_cost = get_feature_emotions(cost_good_feature, cost_bad_feature, cost_temp)

        visit_temp = get_feature_keywords(visit_good_feature.keys(), review)
        good_visit,bad_visit = get_feature_emotions(visit_good_feature, visit_bad_feature, visit_temp)

        taste_temp = get_feature_keywords(taste_good_feature.keys(), review)
        good_taste,bad_taste = get_feature_emotions(taste_good_feature, taste_bad_feature, taste_temp)
        taste_good_emotion_temp = get_feature_keywords(taste_good_emotion, review)
        taste_bad_emotion_temp = get_feature_keywords(taste_bad_emotion, review)
        good_taste2, bad_taste2 = get_taste_emotion(taste_good_emotion_temp,taste_bad_emotion_temp)
        good_taste.extend(good_taste2)
        bad_taste.extend(bad_taste2)

        if len(good_service) > len(bad_service):
            restaurant_good_service_count += 1
        elif len(good_service) < len(bad_service):
            restaurant_bad_service_count += 1
        else:
            pass
        
        if len(good_atmosphere) > len(bad_atmosphere):
            restaurant_good_atmosphere_count += 1
        elif len(good_atmosphere) < len(bad_atmosphere):
            restaurant_bad_atmosphere_count += 1
        else:
            pass
        
        if len(good_cost) > len(bad_cost):
            restaurant_good_cost_count += 1
        elif len(good_cost) < len(bad_cost):
            restaurant_bad_cost_count += 1
        else:
            pass
            
        if len(good_visit) > len(bad_visit):
            restaurant_good_visit_count += 1
        elif len(good_visit) < len(bad_visit):
            restaurant_bad_visit_count += 1
        else:
            pass
        
        if len(good_taste) > len(bad_taste):
            restaurant_good_taste_count += 1
        elif len(good_taste) < len(bad_taste):
            restaurant_bad_taste_count += 1
        else:
            pass
    
    print 'Total review count: {}'.format(len(reviews_list))
    print 'Good service: {}/{} = {}'.format(restaurant_good_service_count,restaurant_good_service_count + restaurant_bad_service_count,check_division(restaurant_good_service_count, restaurant_good_service_count + restaurant_bad_service_count) )
    print 'Bad service: {}/{} = {}'.format(restaurant_bad_service_count,restaurant_good_service_count + restaurant_bad_service_count, check_division(restaurant_bad_service_count, restaurant_good_service_count + restaurant_bad_service_count))
    print 'Good atmosphere: {}/{} = {}'.format(restaurant_good_atmosphere_count,restaurant_good_atmosphere_count + restaurant_bad_atmosphere_count,check_division(restaurant_good_atmosphere_count,restaurant_good_atmosphere_count + restaurant_bad_atmosphere_count)) 
    print 'Bad atmosphere: {}/{} = {}'.format(restaurant_bad_atmosphere_count,restaurant_good_atmosphere_count + restaurant_bad_atmosphere_count, check_division(restaurant_bad_atmosphere_count ,restaurant_good_atmosphere_count + restaurant_bad_atmosphere_count))
    print 'Good cost: {}/{} = {}'.format(restaurant_good_cost_count,restaurant_good_cost_count + restaurant_bad_cost_count, check_division(restaurant_good_cost_count,restaurant_good_cost_count + restaurant_bad_cost_count))
    print 'Bad cost: {}/{} = {}'.format(restaurant_bad_cost_count,restaurant_good_cost_count + restaurant_bad_cost_count, check_division(restaurant_bad_cost_count,restaurant_good_cost_count + restaurant_bad_cost_count))
    print 'Good taste: {}/{} = {}'.format(restaurant_good_taste_count,restaurant_good_taste_count + restaurant_bad_taste_count,check_division(restaurant_good_taste_count,restaurant_good_taste_count + restaurant_bad_taste_count))
    print 'Bad taste: {}/{} = {}'.format(restaurant_bad_taste_count,restaurant_good_taste_count + restaurant_bad_taste_count,check_division(restaurant_bad_taste_count,restaurant_good_taste_count + restaurant_bad_taste_count))
    print

0 베테랑분식-센트럴시티 터미널
Total review count: 35
Good service: 1/2 = 0.5
Bad service: 1/2 = 0.5
Good atmosphere: 0/0 = 0
Bad atmosphere: 0/0 = 0
Good cost: 1/5 = 0.2
Bad cost: 4/5 = 0.8
Good taste: 18/21 = 0.86
Bad taste: 3/21 = 0.14

1 데블스도어-파미에가든
Total review count: 67
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 12/15 = 0.8
Bad atmosphere: 3/15 = 0.2
Good cost: 3/13 = 0.23
Bad cost: 10/13 = 0.77
Good taste: 24/32 = 0.75
Bad taste: 8/32 = 0.25

2 톰볼라-서래점
Total review count: 25
Good service: 2/2 = 1.0
Bad service: 0/2 = 0.0
Good atmosphere: 3/4 = 0.75
Bad atmosphere: 1/4 = 0.25
Good cost: 2/4 = 0.5
Bad cost: 2/4 = 0.5
Good taste: 7/9 = 0.78
Bad taste: 2/9 = 0.22

3 브루클린더버거조인트-본점
Total review count: 83
Good service: 0/1 = 0.0
Bad service: 1/1 = 1.0
Good atmosphere: 1/1 = 1.0
Bad atmosphere: 0/1 = 0.0
Good cost: 4/4 = 1.0
Bad cost: 0/4 = 0.0
Good taste: 28/33 = 0.85
Bad taste: 5/33 = 0.15

4 구슬함박-홍대본점
Total review count: 32
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmo

Total review count: 76
Good service: 3/3 = 1.0
Bad service: 0/3 = 0.0
Good atmosphere: 1/1 = 1.0
Bad atmosphere: 0/1 = 0.0
Good cost: 3/6 = 0.5
Bad cost: 3/6 = 0.5
Good taste: 37/46 = 0.8
Bad taste: 9/46 = 0.2

38 몽고네
Total review count: 30
Good service: 3/3 = 1.0
Bad service: 0/3 = 0.0
Good atmosphere: 3/3 = 1.0
Bad atmosphere: 0/3 = 0.0
Good cost: 3/3 = 1.0
Bad cost: 0/3 = 0.0
Good taste: 17/20 = 0.85
Bad taste: 3/20 = 0.15

39 마키노차야-역삼점
Total review count: 41
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 1/1 = 1.0
Bad atmosphere: 0/1 = 0.0
Good cost: 1/9 = 0.11
Bad cost: 8/9 = 0.89
Good taste: 12/13 = 0.92
Bad taste: 1/13 = 0.08

40 우동명가기리야마
Total review count: 42
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 3/3 = 1.0
Bad atmosphere: 0/3 = 0.0
Good cost: 2/7 = 0.29
Bad cost: 5/7 = 0.71
Good taste: 25/30 = 0.83
Bad taste: 5/30 = 0.17

41 킹콩스테이크
Total review count: 35
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 2/2 = 1.0
Bad atmosphere: 0/2

Total review count: 48
Good service: 0/1 = 0.0
Bad service: 1/1 = 1.0
Good atmosphere: 1/1 = 1.0
Bad atmosphere: 0/1 = 0.0
Good cost: 2/2 = 1.0
Bad cost: 0/2 = 0.0
Good taste: 11/16 = 0.69
Bad taste: 5/16 = 0.31

75 지노스뉴욕피자
Total review count: 59
Good service: 4/7 = 0.57
Bad service: 3/7 = 0.43
Good atmosphere: 4/5 = 0.8
Bad atmosphere: 1/5 = 0.2
Good cost: 0/2 = 0.0
Bad cost: 2/2 = 1.0
Good taste: 30/38 = 0.79
Bad taste: 8/38 = 0.21

76 맛이차이나
Total review count: 54
Good service: 1/2 = 0.5
Bad service: 1/2 = 0.5
Good atmosphere: 1/1 = 1.0
Bad atmosphere: 0/1 = 0.0
Good cost: 9/10 = 0.9
Bad cost: 1/10 = 0.1
Good taste: 35/42 = 0.83
Bad taste: 7/42 = 0.17

77 올리아 키친 앤 그로서리(공사중)
Total review count: 27
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 4/4 = 1.0
Bad atmosphere: 0/4 = 0.0
Good cost: 1/7 = 0.14
Bad cost: 6/7 = 0.86
Good taste: 9/12 = 0.75
Bad taste: 3/12 = 0.25

78 셰막
Total review count: 25
Good service: 0/1 = 0.0
Bad service: 1/1 = 1.0
Good atmosphere: 6/6 = 1.

Total review count: 134
Good service: 3/6 = 0.5
Bad service: 3/6 = 0.5
Good atmosphere: 1/4 = 0.25
Bad atmosphere: 3/4 = 0.75
Good cost: 2/7 = 0.29
Bad cost: 5/7 = 0.71
Good taste: 86/99 = 0.87
Bad taste: 13/99 = 0.13

112 김덕후의곱창조
Total review count: 53
Good service: 5/8 = 0.63
Bad service: 3/8 = 0.38
Good atmosphere: 0/0 = 0
Bad atmosphere: 0/0 = 0
Good cost: 2/3 = 0.67
Bad cost: 1/3 = 0.33
Good taste: 24/31 = 0.77
Bad taste: 7/31 = 0.23

113 라이포스트
Total review count: 178
Good service: 4/4 = 1.0
Bad service: 0/4 = 0.0
Good atmosphere: 2/3 = 0.67
Bad atmosphere: 1/3 = 0.33
Good cost: 6/10 = 0.6
Bad cost: 4/10 = 0.4
Good taste: 84/102 = 0.82
Bad taste: 18/102 = 0.18

114 마렘마-해방촌 쿠촐로 2호점
Total review count: 70
Good service: 5/6 = 0.83
Bad service: 1/6 = 0.17
Good atmosphere: 6/8 = 0.75
Bad atmosphere: 2/8 = 0.25
Good cost: 5/14 = 0.36
Bad cost: 9/14 = 0.64
Good taste: 32/40 = 0.8
Bad taste: 8/40 = 0.2

115 로야토야-홍대점
Total review count: 91
Good service: 3/3 = 1.0
Bad service: 0/3 = 0.0
Goo

Total review count: 61
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 0/1 = 0.0
Bad atmosphere: 1/1 = 1.0
Good cost: 0/4 = 0.0
Bad cost: 4/4 = 1.0
Good taste: 8/13 = 0.62
Bad taste: 5/13 = 0.38

150 매덕스피자
Total review count: 40
Good service: 3/4 = 0.75
Bad service: 1/4 = 0.25
Good atmosphere: 2/2 = 1.0
Bad atmosphere: 0/2 = 0.0
Good cost: 1/2 = 0.5
Bad cost: 1/2 = 0.5
Good taste: 18/24 = 0.75
Bad taste: 6/24 = 0.25

151 프리모바치오바치
Total review count: 48
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 2/2 = 1.0
Bad atmosphere: 0/2 = 0.0
Good cost: 12/14 = 0.86
Bad cost: 2/14 = 0.14
Good taste: 17/23 = 0.74
Bad taste: 6/23 = 0.26

152 모우모우
Total review count: 34
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 0/2 = 0.0
Bad atmosphere: 2/2 = 1.0
Good cost: 0/5 = 0.0
Bad cost: 5/5 = 1.0
Good taste: 14/18 = 0.78
Bad taste: 4/18 = 0.22

153 타르틴-2호점
Total review count: 47
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 0/1 = 0.0
Bad atmos

Total review count: 28
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 2/2 = 1.0
Bad atmosphere: 0/2 = 0.0
Good cost: 4/5 = 0.8
Bad cost: 1/5 = 0.2
Good taste: 13/16 = 0.81
Bad taste: 3/16 = 0.19

187 에이프릴마켓
Total review count: 32
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 6/6 = 1.0
Bad atmosphere: 0/6 = 0.0
Good cost: 0/1 = 0.0
Bad cost: 1/1 = 1.0
Good taste: 16/17 = 0.94
Bad taste: 1/17 = 0.06

188 육회자매집
Total review count: 68
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 2/4 = 0.5
Bad atmosphere: 2/4 = 0.5
Good cost: 12/15 = 0.8
Bad cost: 3/15 = 0.2
Good taste: 30/30 = 1.0
Bad taste: 0/30 = 0.0

189 리프레쉬 5.7-연남동점
Total review count: 50
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 4/4 = 1.0
Bad atmosphere: 0/4 = 0.0
Good cost: 10/15 = 0.67
Bad cost: 5/15 = 0.33
Good taste: 35/36 = 0.97
Bad taste: 1/36 = 0.03

190 베러댄비프
Total review count: 50
Good service: 0/0 = 0
Bad service: 0/0 = 0
Good atmosphere: 7/8 = 0.88
Bad atmosph

Total review count: 75
Good service: 1/3 = 0.33
Bad service: 2/3 = 0.67
Good atmosphere: 0/0 = 0
Bad atmosphere: 0/0 = 0
Good cost: 7/11 = 0.64
Bad cost: 4/11 = 0.36
Good taste: 34/37 = 0.92
Bad taste: 3/37 = 0.08

224 우마이도-건대점
Total review count: 92
Good service: 3/3 = 1.0
Bad service: 0/3 = 0.0
Good atmosphere: 0/0 = 0
Bad atmosphere: 0/0 = 0
Good cost: 4/8 = 0.5
Bad cost: 4/8 = 0.5
Good taste: 33/56 = 0.59
Bad taste: 23/56 = 0.41

225 페르시안걸프
Total review count: 39
Good service: 1/2 = 0.5
Bad service: 1/2 = 0.5
Good atmosphere: 1/2 = 0.5
Bad atmosphere: 1/2 = 0.5
Good cost: 9/11 = 0.82
Bad cost: 2/11 = 0.18
Good taste: 8/14 = 0.57
Bad taste: 6/14 = 0.43

226 오가와
Total review count: 25
Good service: 4/4 = 1.0
Bad service: 0/4 = 0.0
Good atmosphere: 4/4 = 1.0
Bad atmosphere: 0/4 = 0.0
Good cost: 7/12 = 0.58
Bad cost: 5/12 = 0.42
Good taste: 15/17 = 0.88
Bad taste: 2/17 = 0.12

227 리틀파파포-합정1호점
Total review count: 81
Good service: 1/1 = 1.0
Bad service: 0/1 = 0.0
Good atmosphere: 0/0 = 0